In [103]:
import pandas as pd
import numpy as np
import pandas_profiling as pd_prof
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_val_score
from sklearn.tree import DecisionTreeClassifier

In [40]:
train = pd.read_csv("../data/train_1.csv", sep="\t", index_col="Unnamed: 0")
test = pd.read_csv("../data/test_1.csv", sep="\t", index_col="Unnamed: 0")

In [41]:
train.head()

0  1  2  3  4  5  6         7  8  9 ...        336  337  338  339  340  \
0  1  1  0  0  0  0  0  0.090909  0  0 ...   0.221395    0    1    0    0   
1  1  1  0  0  1  0  0  0.090909  0  0 ...   0.241508    0    1    0    0   
2  0  1  0  0  1  0  0  0.090909  0  0 ...   0.123067    0    1    0    0   
3  0  1  0  0  1  0  0  0.136364  0  0 ...   0.296065    0    0    1    0   
4  0  1  0  0  1  0  0  0.136364  0  0 ...   0.178956    0    0    1    0   

        341  342  343  344  345  
0  0.222222    1    1    1    1  
1  0.111111    1    1    1    0  
2  0.444444    1    1    1    1  
3  0.222222    1    1    1    0  
4  0.111111    1    1    1    1  

[5 rows x 346 columns]

In [77]:
x_train = train.iloc[:, 1:]
y_train = train.iloc[:, 0]

In [78]:
x_train.shape, y_train.shape

((30500, 345), (30500,))

In [79]:
y_train.head


<bound method NDFrame.head of 0        1
1        1
2        0
3        0
4        0
5        0
6        0
7        0
8        0
9        0
10       0
11       0
12       0
13       1
14       0
15       0
16       0
17       0
18       1
19       0
20       1
21       1
22       0
23       0
24       1
25       0
26       0
27       0
28       0
29       0
        ..
30470    0
30471    0
30472    0
30473    0
30474    1
30475    0
30476    0
30477    0
30478    0
30479    1
30480    0
30481    0
30482    0
30483    0
30484    0
30485    0
30486    0
30487    0
30488    0
30489    0
30490    0
30491    0
30492    0
30493    0
30494    1
30495    0
30496    0
30497    0
30498    0
30499    0
Name: 0, Length: 30500, dtype: int64>

In [54]:

pr = pd_prof.ProfileReport(x_train)
pr

In [55]:
rejected_variables = pr.get_rejected_variables(threshold=0.9)
print(rejected_variables)

['117', '119', '122', '146', '148', '153', '158', '165', '179', '180', '206', '323', '324', '325', '326', '327', '333', '334', '335', '341', '9']


In [56]:
x_train.shape

(30500, 345)

In [58]:
x_train = x_train.drop(rejected_variables, axis=1, errors='ignore')
x_train.shape

(30500, 324)

In [65]:
kf = StratifiedKFold(n_splits=5, random_state=42)

In [71]:
list(kf.split(x_train, y_train))

[(array([ 6034,  6035,  6037, ..., 30497, 30498, 30499]),
  array([   0,    1,    2, ..., 6392, 6397, 6401])),
 (array([    0,     1,     2, ..., 30497, 30498, 30499]),
  array([ 6034,  6035,  6037, ..., 12220, 12222, 12224])),
 (array([    0,     1,     2, ..., 30497, 30498, 30499]),
  array([12191, 12192, 12193, ..., 18374, 18382, 18386])),
 (array([    0,     1,     2, ..., 30497, 30498, 30499]),
  array([18288, 18289, 18290, ..., 24413, 24414, 24415])),
 (array([    0,     1,     2, ..., 24413, 24414, 24415]),
  array([24298, 24300, 24308, ..., 30497, 30498, 30499]))]

In [86]:
lr = LogisticRegression(random_state=42, class_weight= 'balanced')

In [117]:
scores_lr = cross_val_score(
    estimator=lr,
    X=x_train, # ...
    y=y_train, # ...
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('LR scoring: {:.5f}'.format(scores_lr))

LR scoring: 0.72441


In [104]:
## Decision Tree
dt = DecisionTreeClassifier(max_depth=25, random_state=42)


In [118]:
scores_dt = cross_val_score(estimator=dt,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('dt scoring: {:.5f}'.format(scores_dt))

dt scoring: 0.53812


In [114]:
##Random Forest
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
rf = RandomForestClassifier(random_state=42,max_depth=25)

In [119]:
scores_rf = cross_val_score(estimator=rf,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('rf scoring: {:.5f}'.format(scores_rf))

rf scoring: 0.67130


In [125]:
rf_fred = RandomForestClassifier(random_state=42, max_depth=15, min_samples_leaf=5, max_features=0.33, n_estimators=50, class_weight='balanced')


In [126]:
scores_rf_fred = cross_val_score(estimator=rf_fred,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('fred\'s rf scoring: {:.5f}'.format(scores_rf_fred))

fred's rf scoring: 0.72879


In [135]:
## Grid Search
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
params = {
    'max_depth':[5,10,15,20,25],
    'min_samples_leaf': [2,4,8,16],
    'max_features': [0.33, 0.50, 0.66, 1.0],
    'n_estimators': [2, 4, 8, 16, 32, 64]
    
    
}
gs = RandomizedSearchCV(estimator=rf, param_distributions=params, n_jobs=8, cv=kf, scoring='roc_auc', verbose=2)

In [136]:
gs.fit(x_train, y_train)

Fitting 5 folds for each of 10 candidates, totalling 50 fits
[CV] n_estimators=32, min_samples_leaf=4, max_features=1.0, max_depth=10 
[CV] n_estimators=32, min_samples_leaf=4, max_features=1.0, max_depth=10 
[CV] n_estimators=32, min_samples_leaf=4, max_features=1.0, max_depth=10 
[CV] n_estimators=32, min_samples_leaf=4, max_features=1.0, max_depth=10 
[CV] n_estimators=32, min_samples_leaf=4, max_features=1.0, max_depth=10 
[CV] n_estimators=64, min_samples_leaf=16, max_features=0.33, max_depth=15 
[CV] n_estimators=64, min_samples_leaf=16, max_features=0.33, max_depth=15 
[CV] n_estimators=64, min_samples_leaf=16, max_features=0.33, max_depth=15 
[CV]  n_estimators=64, min_samples_leaf=16, max_features=0.33, max_depth=15, total=  36.2s
[CV] n_estimators=64, min_samples_leaf=16, max_features=0.33, max_depth=15 
[CV]  n_estimators=64, min_samples_leaf=16, max_features=0.33, max_depth=15, total=  36.4s
[CV] n_estimators=64, min_samples_leaf=16, max_features=0.33, max_depth=15 
[CV]  n

[Parallel(n_jobs=8)]: Done  25 tasks      | elapsed:  1.9min


[CV]  n_estimators=16, min_samples_leaf=2, max_features=0.66, max_depth=5, total=   6.8s
[CV] n_estimators=16, min_samples_leaf=2, max_features=0.66, max_depth=5 
[CV]  n_estimators=16, min_samples_leaf=2, max_features=0.66, max_depth=5, total=   7.3s
[CV] n_estimators=16, min_samples_leaf=2, max_features=0.66, max_depth=5 
[CV]  n_estimators=16, min_samples_leaf=2, max_features=0.66, max_depth=5, total=   7.3s
[CV] n_estimators=2, min_samples_leaf=2, max_features=1.0, max_depth=15 
[CV]  n_estimators=2, min_samples_leaf=2, max_features=1.0, max_depth=15, total=   4.1s
[CV] n_estimators=2, min_samples_leaf=2, max_features=1.0, max_depth=15 
[CV]  n_estimators=16, min_samples_leaf=2, max_features=0.66, max_depth=25, total=  27.3s
[CV] n_estimators=2, min_samples_leaf=2, max_features=1.0, max_depth=15 
[CV]  n_estimators=16, min_samples_leaf=2, max_features=0.66, max_depth=5, total=   7.5s
[CV] n_estimators=2, min_samples_leaf=2, max_features=1.0, max_depth=15 
[CV]  n_estimators=2, min_

[Parallel(n_jobs=8)]: Done  50 out of  50 | elapsed:  3.8min finished


RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=False),
          error_score='raise',
          estimator=RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=25, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=1,
            oob_score=False, random_state=42, verbose=0, warm_start=False),
          fit_params=None, iid=True, n_iter=10, n_jobs=8,
          param_distributions={'max_depth': [5, 10, 15, 20, 25], 'min_samples_leaf': [2, 4, 8, 16], 'max_features': [0.33, 0.5, 0.66, 1.0], 'n_estimators': [2, 4, 8, 16, 32, 64]},
          pre_dispatch='2*n_jobs', random_state=None, refit=True,
          return_train_score='warn', scoring='roc_auc', verbose=2)

In [140]:
print("RF RandomizedSearchCV:\nBest Score: {}\nBest Params: {}".format(gs.best_score_, gs.best_params_))


RF RandomizedSearchCV:
Best Score: 0.7325192563609609
Best Params: {'n_estimators': 64, 'min_samples_leaf': 16, 'max_features': 0.33, 'max_depth': 15}


In [141]:
##Rf with best params
best_rf = RandomForestClassifier(random_state=42,max_depth=15, n_estimators=64, min_samples_leaf=16, max_features=0.33)

In [142]:
scores_best_rf = cross_val_score(estimator=best_rf,
                           X=x_train,
                           y=y_train,
                           scoring='roc_auc',
                           cv=kf,
                           n_jobs=8).mean()
print('best rf scoring: {:.5f}'.format(scores_best_rf))

best rf scoring: 0.73252


In [147]:
## Light
import lightgbm as lgb

In [168]:
n_rounds = 10000

lgb_train = lgb.Dataset(x_train, y_train, free_raw_data=False)

In [170]:
parameters = {
    'objective': 'binary',
    'num_threads': 8,
    "metric": 'auc',
    
    
    'colsample_bytree': 0.8,
    'subsample': 0.8,
    'subsample_freq': 1,
    'min_data_in_leaf': 15,
    'num_leaves': 25,
    #categorical features
    'cat_smooth': 10,
    'min_data_per_group': 50
}

result = lgb.cv(parameters, lgb_train, n_rounds, folds=kf.split(x_train, y_train), early_stopping_rounds=45, verbose_eval=0, )
print(max(result['auc-mean']), len(result['auc-mean']))

0.7450115942907046 714


In [ ]:

est = lgb.LGBMClassifier(objective='binary', num_threads=8, metric='auc')
param_grid = {
    'learning_rate': [0.01, 0.1, 1],
    'n_estimators': [20, 40],
    #regularization
    'colsample_bytree': [0.6, 0.8, 1.0],
    'subsample': [0.6,0.8, 1.0],
    'subsample_freq': [1],
    'min_data_in_leaf': [5,10,15,20],
    
    #categorical features
    'cat_smooth': [5, 10, 15, 20],
    'min_data_per_group': [10, 20 ,30 ,40 ,50],
    
}

gbm =GridSearchCV(est, param_grid, n_jobs=8, cv=kf, scoring='roc_auc', verbose=-2)

gbm.fit(x_train, y_train, )
print("RF RandomizedSearchCV:\nBest Score: {}\nBest Params: {}".format(gbm.best_score_, gbm.best_params_))

[Parallel(n_jobs=8)]: Done  69 tasks      | elapsed:  1.3min
[Parallel(n_jobs=8)]: Done 322 tasks      | elapsed:  6.4min
[Parallel(n_jobs=8)]: Done 745 tasks      | elapsed: 15.0min
[Parallel(n_jobs=8)]: Done 1336 tasks      | elapsed: 26.7min
[Parallel(n_jobs=8)]: Done 2097 tasks      | elapsed: 42.0min


In [85]:
## Bagging LR
from sklearn.ensemble import BaggingClassifier

In [95]:
bg = BaggingClassifier(lr, random_state=42, n_estimators=15)

In [120]:
scores_bg = cross_val_score(
    estimator=bg,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('BG scoring: {:.5f}'.format(scores_bg))

BG scoring: 0.72378


In [108]:
##Bagging DT
bg_dt = BaggingClassifier(dt, random_state=42, n_estimators=15)

In [121]:
scores_bg_dt = cross_val_score(
    estimator=bg_dt,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('BG_dt scoring: {:.5f}'.format(scores_bg_dt))

BG_dt scoring: 0.69488


In [122]:
##Bagging RF
bg_rf = BaggingClassifier(rf, random_state=42, n_estimators=15)

In [123]:
scores_bg_rf = cross_val_score(
    estimator=bg_rf,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('BG_rf scoring: {:.5f}'.format(scores_bg_rf))

BG_rf scoring: 0.71966


In [145]:
##Bagging Best RF
bg_best_rf = BaggingClassifier(best_rf, random_state=42, n_estimators=15)

In [146]:
scores_bg_best_rf = cross_val_score(
    estimator=bg_best_rf,
    X=x_train,
    y=y_train,
    scoring='roc_auc',
    cv=kf,
    n_jobs=8
).mean()
print('Best BG_rf scoring: {:.5f}'.format(scores_bg_best_rf))

Best BG_rf scoring: 0.73058
